In [2]:
# Notebook bootstrap
from pathlib import Path
import sys, os

PROJECT_ROOT = Path.cwd().resolve()
SRC = PROJECT_ROOT / "src"
if str(SRC) not in sys.path:
    sys.path.insert(0, str(SRC))

from dotenv import load_dotenv
load_dotenv(PROJECT_ROOT / "assets" / "config.env")

%load_ext autoreload
%autoreload 2

import nltk
nltk.download('punkt')       # Sentence tokenizer
nltk.download('stopwords')   # English stopwords
nltk.download('averaged_perceptron_tagger')  # POS tagging (optional)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\joems\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\joems\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\joems\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [3]:

import pandas as pd
import polars as pl
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from pathlib import Path
from itables import init_notebook_mode, show
import warnings
from IPython.display import display, HTML


def display_table_with_html(df, title=""):
    """Display pandas DataFrame as styled HTML table"""
    display(HTML(f"<h3>{title}</h3>"))
    html_str = df.to_html(classes='table table-striped table-hover', border=0)
    display(HTML(html_str))


print("Environment ready")

# Load dataset
DATA_PATH = Path("../data/exports/sec_filings_small_full.parquet")
df = pl.read_parquet(DATA_PATH)

print(f"Dataset loaded: {df.shape[0]:,} rows × {df.shape[1]} columns")
print(f"Memory usage: {df.estimated_size('mb'):.1f} MB")

Environment ready
Dataset loaded: 200,000 rows × 19 columns
Memory usage: 144.1 MB


In [4]:

DATA_PATH = Path("../data/exports/sec_filings_small_full.parquet")
df = pl.read_parquet(DATA_PATH)

print(df.schema)
print("Head is:", df.head(4))
print("Head is:", df.head(4).to_dicts())

print("Type of df is:", type(df))

df.describe()  # Summary statistics



"""
json/html/txt - XRBL format; -> data from edgar API. 

data preprocessing -
   header idenftification, section/semantic identification, table-extraction.... 
   messy data -> fit them into schmea.

   Schema([                                   
        ('cik', String), ('sentence', String), 
        ('section', Int64), ('labels', Struct({'1d': Int64, '30d': Int64, '5d': Int64}))),

        ('filingDate', String), ('name', String), ('docID', String), ('sentenceID', String), 
        ('sentenceCount', Int64),('tickers', List(String)), ('exchanges', List(String)), ('entityType', String), 
        ('sic', String), ('stateOfIncorporation', String), ('tickerCount', Int32), 
        ('acceptanceDateTime', String), ('form', String), ('reportDate', String),

        ('returns', Struct({'1d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String,
                                    'ret': Float64, 'startDate': String}), 
                            '30d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 
                                    'ret': Float64, 'startDate': String}), 
                            '5d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 
                                    'ret': Float64, 'startDate': String})}))]
                        )
"""

Schema([('cik', String), ('sentence', String), ('section', Int64), ('labels', Struct({'1d': Int64, '30d': Int64, '5d': Int64})), ('filingDate', String), ('name', String), ('docID', String), ('sentenceID', String), ('sentenceCount', Int64), ('tickers', List(String)), ('exchanges', List(String)), ('entityType', String), ('sic', String), ('stateOfIncorporation', String), ('tickerCount', Int32), ('acceptanceDateTime', String), ('form', String), ('reportDate', String), ('returns', Struct({'1d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 'ret': Float64, 'startDate': String}), '30d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 'ret': Float64, 'startDate': String}), '5d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 'ret': Float64, 'startDate': String})}))])
Head is: shape: (4, 19)
┌────────────┬─────────────┬─────────┬───────────┬───┬────────────┬──────┬──────

"\njson/html/txt - XRBL format; -> data from edgar API. \n\ndata preprocessing -\n   header idenftification, section/semantic identification, table-extraction.... \n   messy data -> fit them into schmea.\n\n   Schema([                                   \n        ('cik', String), ('sentence', String), \n        ('section', Int64), ('labels', Struct({'1d': Int64, '30d': Int64, '5d': Int64}))),\n\n        ('filingDate', String), ('name', String), ('docID', String), ('sentenceID', String), \n        ('sentenceCount', Int64),('tickers', List(String)), ('exchanges', List(String)), ('entityType', String), \n        ('sic', String), ('stateOfIncorporation', String), ('tickerCount', Int32), \n        ('acceptanceDateTime', String), ('form', String), ('reportDate', String),\n\n        ('returns', Struct({'1d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String,\n                                    'ret': Float64, 'startDate': String}), \n                     

In [ ]:
# null counts and unique values
print(df.null_count())  

print(df.select([pl.all().n_unique()]))

print(df.select([pl.all().n_unique().sum()]))  

shape: (1, 19)
┌─────┬──────────┬─────────┬────────┬───┬────────────────────┬──────┬────────────┬─────────┐
│ cik ┆ sentence ┆ section ┆ labels ┆ … ┆ acceptanceDateTime ┆ form ┆ reportDate ┆ returns │
│ --- ┆ ---      ┆ ---     ┆ ---    ┆   ┆ ---                ┆ ---  ┆ ---        ┆ ---     │
│ u32 ┆ u32      ┆ u32     ┆ u32    ┆   ┆ u32                ┆ u32  ┆ u32        ┆ u32     │
╞═════╪══════════╪═════════╪════════╪═══╪════════════════════╪══════╪════════════╪═════════╡
│ 0   ┆ 0        ┆ 0       ┆ 0      ┆ … ┆ 0                  ┆ 0    ┆ 0          ┆ 0       │
└─────┴──────────┴─────────┴────────┴───┴────────────────────┴──────┴────────────┴─────────┘
shape: (1, 19)
┌─────┬──────────┬─────────┬────────┬───┬────────────────────┬──────┬────────────┬─────────┐
│ cik ┆ sentence ┆ section ┆ labels ┆ … ┆ acceptanceDateTime ┆ form ┆ reportDate ┆ returns │
│ --- ┆ ---      ┆ ---     ┆ ---    ┆   ┆ ---                ┆ ---  ┆ ---        ┆ ---     │
│ u32 ┆ u32      ┆ u32     ┆ u32    ┆   

In [28]:
# pandas (if needed)
pdf = df.to_pandas()

print(pdf.shape)
print(pdf.columns)

# pdf.head(5); pdf.tail(5)
print("printing pandas info", pdf.info())


(200000, 19)
Index(['cik', 'sentence', 'section', 'labels', 'filingDate', 'name', 'docID',
       'sentenceID', 'sentenceCount', 'tickers', 'exchanges', 'entityType',
       'sic', 'stateOfIncorporation', 'tickerCount', 'acceptanceDateTime',
       'form', 'reportDate', 'returns'],
      dtype='object')
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 200000 entries, 0 to 199999
Data columns (total 19 columns):
 #   Column                Non-Null Count   Dtype 
---  ------                --------------   ----- 
 0   cik                   200000 non-null  object
 1   sentence              200000 non-null  object
 2   section               200000 non-null  int64 
 3   labels                200000 non-null  object
 4   filingDate            200000 non-null  object
 5   name                  200000 non-null  object
 6   docID                 200000 non-null  object
 7   sentenceID            200000 non-null  object
 8   sentenceCount         200000 non-null  int64 
 9   tickers           

In [29]:
print("\n=================================================\n")
print(pdf.isna().sum())
print(pdf.describe(include='all'))



cik                     0
sentence                0
section                 0
labels                  0
filingDate              0
name                    0
docID                   0
sentenceID              0
sentenceCount           0
tickers                 0
exchanges               0
entityType              0
sic                     0
stateOfIncorporation    0
tickerCount             0
acceptanceDateTime      0
form                    0
reportDate              0
returns                 0
dtype: int64
               cik sentence        section                        labels  \
count       200000   200000  200000.000000                        200000   
unique          10    96465            NaN                             8   
top     0000002488  ITEM 3.            NaN  {'1d': 1, '30d': 1, '5d': 1}   
freq         38799      222            NaN                         55923   
mean           NaN      NaN       7.844870                           NaN   
std            NaN      NaN       5

In [ ]:
df.select([pl.col("sentenceID").unique().count()])

# unique sentenceIDs as a list
unique_sentence_ids = df.get_column("sentenceID").unique().to_list()
print("Printing unique sentence IDs as a list:", unique_sentence_ids)

#  works but format fails, cant print. odd.


Printing unique sentence IDs as a list: ['0000001961_10-K_2012_section_14_14', '0000001750_10-K_2002_section_8_108', '0000001800_10-K_2019_section_1_115', '0000003197_10-K_2013_section_7_70', '0000003197_10-K_2012_section_15_313', '0000003197_10-K_2010_section_1_240', '0000003197_10-K_2009_section_15_245', '0000002186_10-K_2008_section_1_77', '0000002969_10-K_2009_section_3_1', '0000001800_10-K_2013_section_8_5', '0000001800_10-K_2002_section_8_423', '0000001961_10-K_2011_section_1_18', '0000001800_10-K_2017_section_9A_7', '0000001800_10-K_2014_section_7_133', '0000001800_10-K_2003_section_1_114', '0000002178_10-K_2007_section_8_267', '0000001750_10-K_2017_section_7_43', '0000002488_10-K_2016_section_1A_152', '0000002488_10-K_2008_section_7_5', '0000002488_10-K_2003_section_8_424', '0000003197_10-K_2010_section_15_219', '0000002178_10-K_2019_section_1A_57', '0000003197_10-K_2017_section_1A_26', '0000003197_10-K_2014_section_1_18', '0000003197_10-K_2014_section_7_220', '0000003197_10-K_

In [47]:

# pl.select column-expression syntax
unique_sentence_ids_expr = df.select(pl.col("sentenceID").unique())
print("Printing expr1:",unique_sentence_ids_expr)
print("Type of expr1 is:", type(unique_sentence_ids_expr))

# Understanding an expression:
expr = pl.col("sentenceID").unique()
print("Expression object:", expr)
# To evaluate an expression, use it inside df.select([expr])
result = df.select([expr])
print("Result of evaluating the expression:\n", result)



Printing expr1: shape: (200_000, 1)
┌─────────────────────────────────┐
│ sentenceID                      │
│ ---                             │
│ str                             │
╞═════════════════════════════════╡
│ 0000003197_10-K_2005_section_1… │
│ 0000002969_10-K_2012_section_8… │
│ 0000002186_10-K_2018_section_1… │
│ 0000002488_10-K_2007_section_1… │
│ 0000003197_10-K_2015_section_1… │
│ …                               │
│ 0000001800_10-K_2008_section_1… │
│ 0000003197_10-K_2010_section_7… │
│ 0000002488_10-K_2008_section_8… │
│ 0000002488_10-K_2009_section_8… │
│ 0000002969_10-K_2017_section_8… │
└─────────────────────────────────┘
Type of expr1 is: <class 'polars.dataframe.frame.DataFrame'>
Expression object: col("sentenceID").unique()
Result of evaluating the expression:
 shape: (200_000, 1)
┌─────────────────────────────────┐
│ sentenceID                      │
│ ---                             │
│ str                             │
╞═════════════════════════════════╡
│ 00000

In [52]:

## similar to a select in SQL
df.select([pl.col("sentenceID"), pl.col("sentence"), pl.col("section"), pl.col("reportDate")]).head(10)



shape: (10, 4)
┌─────────────────────────────────┬─────────────────────────────────┬─────────┬────────────┐
│ sentenceID                      ┆ sentence                        ┆ section ┆ reportDate │
│ ---                             ┆ ---                             ┆ ---     ┆ ---        │
│ str                             ┆ str                             ┆ i64     ┆ str        │
╞═════════════════════════════════╪═════════════════════════════════╪═════════╪════════════╡
│ 0000001750_10-K_2020_section_1… ┆ ITEM 1.BUSINESS General AAR CO… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ AAR was founded in 1951, organ… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ We are a diversified provider … ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ Fiscal 2020 began with strateg… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ Our momentum from a successful… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ We also realized the positive … ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ We succeeded in enhancing cust… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ In fiscal 2020, we were awarde… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ This award demonstrates the po… ┆ 0       ┆ 2020-05-31 │
│ 0000001750_10-K_2020_section_1… ┆ We were also awarded new long-… ┆ 0       ┆ 2020-05-31 │
└─────────────────────────────────┴─────────────────────────────────┴─────────┴────────────┘

In [53]:
print("\n=================================================\n")
pdf["section"].value_counts(dropna=False, normalize=False)


section
10    60256
8     47677
1     24627
0     21311
19    14312
4      4534
9      3993
5      3893
14     3166
12     2906
6      2836
3      2317
16     1889
18     1681
7      1355
15     1125
17      661
11      608
13      479
2       374
Name: count, dtype: int64

In [58]:
## random sampling.
# df.sample(n=2, with_replacement=False, seed=42)

In [60]:

# select a random sentenceID and filter the dataframe
rid = df.select(pl.col("sentenceID").sample(1, with_replacement=False, seed=42)).to_series()[0]
rid2 = df.filter(pl.col("sentenceID") == rid)
print("Randomly selected sentenceID:", rid)
print("Filtered dataframe for that sentenceID:\n", rid2)

Randomly selected sentenceID: 0000002969_10-K_2013_section_8_642
Filtered dataframe for that sentenceID:
 shape: (1, 19)
┌────────────┬─────────────┬─────────┬───────────┬───┬────────────┬──────┬────────────┬────────────┐
│ cik        ┆ sentence    ┆ section ┆ labels    ┆ … ┆ acceptance ┆ form ┆ reportDate ┆ returns    │
│ ---        ┆ ---         ┆ ---     ┆ ---       ┆   ┆ DateTime   ┆ ---  ┆ ---        ┆ ---        │
│ str        ┆ str         ┆ i64     ┆ struct[3] ┆   ┆ ---        ┆ str  ┆ str        ┆ struct[3]  │
│            ┆             ┆         ┆           ┆   ┆ str        ┆      ┆            ┆            │
╞════════════╪═════════════╪═════════╪═══════════╪═══╪════════════╪══════╪════════════╪════════════╡
│ 0000002969 ┆ Expected    ┆ 10      ┆ {1,0,1}   ┆ … ┆ 2013-11-26 ┆ 10-K ┆ 2013-09-30 ┆ {{81.37815 │
│            ┆ volatility  ┆         ┆           ┆   ┆ T09:38:11. ┆      ┆            ┆ 9,81.8256, │
│            ┆ and expect… ┆         ┆           ┆   ┆ 000Z       ┆    

In [ ]:
o1 = df.select(["sentenceID","section","docID","reportDate","sentence"]).head(5)
print("o1 is:", o1)


o1 is: shape: (5, 5)
┌──────────────────────────┬─────────┬──────────────────────┬────────────┬─────────────────────────┐
│ sentenceID               ┆ section ┆ docID                ┆ reportDate ┆ sentence                │
│ ---                      ┆ ---     ┆ ---                  ┆ ---        ┆ ---                     │
│ str                      ┆ i64     ┆ str                  ┆ str        ┆ str                     │
╞══════════════════════════╪═════════╪══════════════════════╪════════════╪═════════════════════════╡
│ 0000001750_10-K_2020_sec ┆ 0       ┆ 0000001750_10-K_2020 ┆ 2020-05-31 ┆ ITEM 1.BUSINESS General │
│ tion_1…                  ┆         ┆                      ┆            ┆ AAR CO…                 │
│ 0000001750_10-K_2020_sec ┆ 0       ┆ 0000001750_10-K_2020 ┆ 2020-05-31 ┆ AAR was founded in      │
│ tion_1…                  ┆         ┆                      ┆            ┆ 1951, organ…            │
│ 0000001750_10-K_2020_sec ┆ 0       ┆ 0000001750_10-K_2020 ┆ 2020-05-

shape: (10, 2)
┌────────────────────────────────┬───────┐
│ name                           ┆ len   │
│ ---                            ┆ ---   │
│ str                            ┆ u32   │
╞════════════════════════════════╪═══════╡
│ ADVANCED MICRO DEVICES INC     ┆ 38799 │
│ ABBOTT LABORATORIES            ┆ 30554 │
│ Air Products & Chemicals, Inc. ┆ 26282 │
│ CECO ENVIRONMENTAL CORP        ┆ 24867 │
│ AAR CORP                       ┆ 20350 │
│ BK Technologies Corp           ┆ 19081 │
│ ACME UNITED CORP               ┆ 15849 │
│ ADAMS RESOURCES & ENERGY, INC. ┆ 14964 │
│ WORLDS INC                     ┆ 7797  │
│ Matson, Inc.                   ┆ 1457  │
└────────────────────────────────┴───────┘

In [77]:

print(df.group_by("section").len().sort("len", descending=True).head(5))

print(df.group_by("section").len("sentenceID").sort("sentenceID", descending=True).head(5))

shape: (5, 2)
┌─────────┬───────┐
│ section ┆ len   │
│ ---     ┆ ---   │
│ i64     ┆ u32   │
╞═════════╪═══════╡
│ 10      ┆ 60256 │
│ 8       ┆ 47677 │
│ 1       ┆ 24627 │
│ 0       ┆ 21311 │
│ 19      ┆ 14312 │
└─────────┴───────┘
shape: (5, 2)
┌─────────┬────────────┐
│ section ┆ sentenceID │
│ ---     ┆ ---        │
│ i64     ┆ u32        │
╞═════════╪════════════╡
│ 10      ┆ 60256      │
│ 8       ┆ 47677      │
│ 1       ┆ 24627      │
│ 0       ┆ 21311      │
│ 19      ┆ 14312      │
└─────────┴────────────┘


shape: (10, 2)
┌────────────────────────────────┬───────┐
│ name                           ┆ len   │
│ ---                            ┆ ---   │
│ str                            ┆ u32   │
╞════════════════════════════════╪═══════╡
│ ADVANCED MICRO DEVICES INC     ┆ 38799 │
│ ABBOTT LABORATORIES            ┆ 30554 │
│ Air Products & Chemicals, Inc. ┆ 26282 │
│ CECO ENVIRONMENTAL CORP        ┆ 24867 │
│ AAR CORP                       ┆ 20350 │
│ BK Technologies Corp           ┆ 19081 │
│ ACME UNITED CORP               ┆ 15849 │
│ ADAMS RESOURCES & ENERGY, INC. ┆ 14964 │
│ WORLDS INC                     ┆ 7797  │
│ Matson, Inc.                   ┆ 1457  │
└────────────────────────────────┴───────┘

## Accessing struct fields and money etc.  

In [41]:
""" Think SQL: 
GROUP BY -> AGG -> ORDER BY -> LIMIT, but in Polars it’s group_by().agg().sort().head().
Nested fields (like returns.5d.ret) → pl.col("returns").struct.field("5d").struct.field("ret").
Window ranks → build a sorted frame, then .with_columns(int_range(...).over(group)).
Shares = divide by a total (global or per-group) → use joins or .over("group") windows for per-group totals.
"""


# Per-Section: distinct docs + sentence count + min/max/avg returns
# 1) define numeric expressions from the nested struct
ret_1d  = pl.col("returns").struct.field("1d").struct.field("ret")
ret_5d  = pl.col("returns").struct.field("5d").struct.field("ret")
ret_30d = pl.col("returns").struct.field("30d").struct.field("ret")

ddocs = (
    df.group_by("section")
      .agg([
          pl.len().alias("n_sentences"),                             # count of rows in group
          pl.col("docID").n_unique().alias("distinct_docs"),         # distinct filings
          pl.col("sentenceID").n_unique().alias("distinct_sentenceIDs"),
          # numeric stats from nested returns
          ret_1d.min().alias("ret1d_min"),
          ret_1d.max().alias("ret1d_max"),
          ret_1d.mean().alias("ret1d_avg"),
          ret_5d.mean().alias("ret5d_avg"),
          ret_30d.mean().alias("ret30d_avg"),
      ])
      .sort("n_sentences", descending=True)
)

ddocs.head(10)


shape: (10, 9)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ section ┆ n_sentence ┆ distinct_ ┆ distinct_ ┆ … ┆ ret1d_max ┆ ret1d_avg ┆ ret5d_avg ┆ ret30d_av │
│ ---     ┆ s          ┆ docs      ┆ sentenceI ┆   ┆ ---       ┆ ---       ┆ ---       ┆ g         │
│ i64     ┆ ---        ┆ ---       ┆ Ds        ┆   ┆ f64       ┆ f64       ┆ f64       ┆ ---       │
│         ┆ u32        ┆ u32       ┆ ---       ┆   ┆           ┆           ┆           ┆ f64       │
│         ┆            ┆           ┆ u32       ┆   ┆           ┆           ┆           ┆           │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 10      ┆ 60256      ┆ 180       ┆ 60256     ┆ … ┆ 0.279805  ┆ -0.003536 ┆ -0.004495 ┆ 0.014951  │
│ 8       ┆ 47677      ┆ 187       ┆ 47677     ┆ … ┆ 0.279805  ┆ -0.000385 ┆ 0.001493  ┆ 0.027423  │
│ 1       ┆ 24627      ┆ 137       ┆ 24627     ┆ … ┆ 0.279805  ┆ 0.003006  ┆ -0.002451 ┆ 0.017609  │
│ 0       ┆ 21311      ┆ 169       ┆ 21311     ┆ … ┆ 0.279805  ┆ -0.003197 ┆ 0.005421  ┆ 0.005661  │
│ 19      ┆ 14312      ┆ 163       ┆ 14312     ┆ … ┆ 0.279805  ┆ 0.017386  ┆ 0.025039  ┆ 0.026001  │
│ 4       ┆ 4534       ┆ 187       ┆ 4534      ┆ … ┆ 0.279805  ┆ -0.006881 ┆ 0.010813  ┆ 0.018612  │
│ 9       ┆ 3993       ┆ 157       ┆ 3993      ┆ … ┆ 0.279805  ┆ -0.00894  ┆ 0.010843  ┆ -0.002421 │
│ 5       ┆ 3893       ┆ 186       ┆ 3893      ┆ … ┆ 0.279805  ┆ -0.004905 ┆ -0.002683 ┆ -0.009421 │
│ 14      ┆ 3166       ┆ 187       ┆ 3166      ┆ … ┆ 0.279805  ┆ -0.005343 ┆ -0.012795 ┆ -0.016542 │
│ 12      ┆ 2906       ┆ 156       ┆ 2906      ┆ … ┆ 0.279805  ┆ 0.002148  ┆ -0.005882 ┆ 0.018951  │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [40]:

print(df.columns)                                
print("\n=================================================\n")

print(df.schema.get("returns"))                    


# OR inspect a single row to see the nested keys:
print(df.select(pl.col("returns")).head(2))
print("\n=================================================\n")

ret_1d = pl.col("returns").struct.field("1d").struct.field("ret")
ret_5d = pl.col("returns").struct.field("5d").struct.field("ret")
ret_30d = pl.col("returns").struct.field("30d").struct.field("ret")

print(
  df.group_by("section")
    .agg([
      pl.len().alias("n_sentences"),
      pl.col("docID").n_unique().alias("n_docs"),
      ret_1d.min().alias("ret1d_min"),
      ret_1d.max().alias("ret1d_max"),
      ret_1d.mean().alias("ret1d_avg"),
      ret_5d.mean().alias("ret5d_avg"),
      ret_30d.mean().alias("ret30d_avg"),
    ])
    .sort("n_sentences", descending=True)
    .head(10)
)


['cik', 'sentence', 'section', 'labels', 'filingDate', 'name', 'docID', 'sentenceID', 'sentenceCount', 'tickers', 'exchanges', 'entityType', 'sic', 'stateOfIncorporation', 'tickerCount', 'acceptanceDateTime', 'form', 'reportDate', 'returns']


Struct({'1d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 'ret': Float64, 'startDate': String}), '30d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 'ret': Float64, 'startDate': String}), '5d': Struct({'closePriceEndDate': Float64, 'closePriceStartDate': Float64, 'endDate': String, 'ret': Float64, 'startDate': String})})
shape: (2, 1)
┌─────────────────────────────────┐
│ returns                         │
│ ---                             │
│ struct[3]                       │
╞═════════════════════════════════╡
│ {{19.01,18.190001,"2020-07-22T… │
│ {{19.01,18.190001,"2020-07-22T… │
└─────────────────────────────────┘


shape: (10, 8)
┌─────────┬─────────────┬

In [4]:
# 0) flatten the nested returns to plain float columns
df_flat = df.with_columns([
    pl.col("returns").struct.field("1d").struct.field("ret").alias("ret_1d"),
    pl.col("returns").struct.field("5d").struct.field("ret").alias("ret_5d"),
    pl.col("returns").struct.field("30d").struct.field("ret").alias("ret_30d"),
])

print("df flat looks like this:", df_flat.head(4))
print("\n=================================================\n")

# 1) now aggregate like SQL
ddocs = (
    df_flat.group_by("section").agg(
        n_sentences          = pl.len(),
        distinct_docs        = pl.col("docID").n_unique(),
        distinct_sentenceIDs = pl.col("sentenceID").n_unique(),
        ret1d_min            = pl.col("ret_1d").min(),
        ret1d_max            = pl.col("ret_1d").max(),
        ret1d_avg            = pl.col("ret_1d").mean(),
        ret5d_avg            = pl.col("ret_5d").mean(),
        ret30d_avg           = pl.col("ret_30d").mean(),
    ).sort("n_sentences", descending=True)
)

ddocs.head(15)


df flat looks like this: shape: (4, 22)
┌────────────┬─────────────┬─────────┬───────────┬───┬────────────┬─────────┬───────────┬──────────┐
│ cik        ┆ sentence    ┆ section ┆ labels    ┆ … ┆ returns    ┆ ret_1d  ┆ ret_5d    ┆ ret_30d  │
│ ---        ┆ ---         ┆ ---     ┆ ---       ┆   ┆ ---        ┆ ---     ┆ ---       ┆ ---      │
│ str        ┆ str         ┆ i64     ┆ struct[3] ┆   ┆ struct[3]  ┆ f64     ┆ f64       ┆ f64      │
╞════════════╪═════════════╪═════════╪═══════════╪═══╪════════════╪═════════╪═══════════╪══════════╡
│ 0000001750 ┆ ITEM        ┆ 0       ┆ {0,0,1}   ┆ … ┆ {{19.01,18 ┆ 0.04508 ┆ -0.025838 ┆ 0.058274 │
│            ┆ 1.BUSINESS  ┆         ┆           ┆   ┆ .190001,"2 ┆         ┆           ┆          │
│            ┆ General AAR ┆         ┆           ┆   ┆ 020-07-22T ┆         ┆           ┆          │
│            ┆ CO…         ┆         ┆           ┆   ┆ …          ┆         ┆           ┆          │
│ 0000001750 ┆ AAR was     ┆ 0       ┆ {0,0,1}   ┆ 

shape: (15, 9)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ section ┆ n_sentence ┆ distinct_ ┆ distinct_ ┆ … ┆ ret1d_max ┆ ret1d_avg ┆ ret5d_avg ┆ ret30d_av │
│ ---     ┆ s          ┆ docs      ┆ sentenceI ┆   ┆ ---       ┆ ---       ┆ ---       ┆ g         │
│ i64     ┆ ---        ┆ ---       ┆ Ds        ┆   ┆ f64       ┆ f64       ┆ f64       ┆ ---       │
│         ┆ u32        ┆ u32       ┆ ---       ┆   ┆           ┆           ┆           ┆ f64       │
│         ┆            ┆           ┆ u32       ┆   ┆           ┆           ┆           ┆           │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 10      ┆ 60256      ┆ 180       ┆ 60256     ┆ … ┆ 0.279805  ┆ -0.003536 ┆ -0.004495 ┆ 0.014951  │
│ 8       ┆ 47677      ┆ 187       ┆ 47677     ┆ … ┆ 0.279805  ┆ -0.000385 ┆ 0.001493  ┆ 0.027423  │
│ 1       ┆ 24627      ┆ 137       ┆ 24627     ┆ … ┆ 0.279805  ┆ 0.003006  ┆ -0.002451 ┆ 0.017609  │
│ 0       ┆ 21311      ┆ 169       ┆ 21311     ┆ … ┆ 0.279805  ┆ -0.003197 ┆ 0.005421  ┆ 0.005661  │
│ 19      ┆ 14312      ┆ 163       ┆ 14312     ┆ … ┆ 0.279805  ┆ 0.017386  ┆ 0.025039  ┆ 0.026001  │
│ …       ┆ …          ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …         │
│ 6       ┆ 2836       ┆ 186       ┆ 2836      ┆ … ┆ 0.279805  ┆ 0.003355  ┆ -0.013518 ┆ 0.023029  │
│ 3       ┆ 2317       ┆ 168       ┆ 2317      ┆ … ┆ 0.279805  ┆ -0.001735 ┆ 0.000075  ┆ 0.009144  │
│ 16      ┆ 1889       ┆ 187       ┆ 1889      ┆ … ┆ 0.279805  ┆ -0.001284 ┆ -0.005236 ┆ -0.001361 │
│ 18      ┆ 1681       ┆ 187       ┆ 1681      ┆ … ┆ 0.279805  ┆ -0.000758 ┆ -0.000471 ┆ -0.030258 │
│ 7       ┆ 1355       ┆ 163       ┆ 1355      ┆ … ┆ 0.279805  ┆ -0.004392 ┆ -0.001799 ┆ 0.013961  │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [23]:
## checking count of years in dataset per company.


# --- derive fiscal year once ---
df_year = df.with_columns(
    pl.col("reportDate").str.strptime(pl.Date, strict=False).dt.year().alias("fiscal_year")
)

# print("df_year:", df_year.head(4))
print("\n=================================================\n")

# --- per-company rollup ---
TOP10 = [10, 8, 1, 0, 19, 4, 9, 5, 6, 3]   # “top 10” by coverage
KPI_CORE = [10, 8, 9, 0, 1]                # recommended hot set KPI RAG

comp_rollup = (
    df_year
    .filter( (pl.col("fiscal_year") > 2014) & (pl.col("section").is_in(TOP10)) )
    .group_by(["cik", "name"])
        .agg(        
            row_count = pl.len(),
            n_years = pl.n_unique("fiscal_year"),
            years_arr = pl.col("fiscal_year").unique().sort(),
            n_docs_filings = pl.col("docID").n_unique(),
            docID_arr = pl.col("docID").unique().sort(),
            n_sentences = pl.col("sentenceID").n_unique(),
            n_sections = pl.col("section").n_unique(),
        )
        .with_columns([
            pl.col("years_arr").list.eval(pl.element().cast(pl.Utf8)).list.join(", ").alias("years"),
            pl.col("docID_arr").list.eval(pl.element().cast(pl.Utf8)).list.join(", ").alias("docIDs")
        ])
        .select("cik","name", "n_years","years","n_docs_filings","docIDs","n_sentences","n_sections")
        .with_columns(
            avg_sentences_per_filing = pl.col("n_sentences") / pl.col("n_docs_filings"),
            avg_sections_per_filing  = pl.col("n_sections") / pl.col("n_docs_filings")
        )
        .sort(["n_docs_filings", "n_years", "n_sentences"], descending=[True, True, True])

)


# print("comp_rollup:", comp_rollup.head(20))
comp_rollup.head(20)

shape: (10, 10)
┌────────────┬───────────┬─────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ cik        ┆ name      ┆ n_years ┆ years     ┆ … ┆ n_sentenc ┆ n_section ┆ avg_sente ┆ avg_secti │
│ ---        ┆ ---       ┆ ---     ┆ ---       ┆   ┆ es        ┆ s         ┆ nces_per_ ┆ ons_per_f │
│ str        ┆ str       ┆ u32     ┆ str       ┆   ┆ ---       ┆ ---       ┆ filing    ┆ iling     │
│            ┆           ┆         ┆           ┆   ┆ u32       ┆ u32       ┆ ---       ┆ ---       │
│            ┆           ┆         ┆           ┆   ┆           ┆           ┆ f64       ┆ f64       │
╞════════════╪═══════════╪═════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 0000002969 ┆ Air       ┆ 6       ┆ 2015,     ┆ … ┆ 11518     ┆ 10        ┆ 1919.6666 ┆ 1.666667  │
│            ┆ Products  ┆         ┆ 2016,     ┆   ┆           ┆           ┆ 67        ┆           │
│            ┆ & Chemica ┆         ┆ 2017,     ┆   ┆           ┆           ┆           ┆           │
│            ┆ ls, Inc.  ┆         ┆ 2018,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2019, …   ┆   ┆           ┆           ┆           ┆           │
│ 0000002488 ┆ ADVANCED  ┆ 6       ┆ 2015,     ┆ … ┆ 9170      ┆ 10        ┆ 1528.3333 ┆ 1.666667  │
│            ┆ MICRO     ┆         ┆ 2016,     ┆   ┆           ┆           ┆ 33        ┆           │
│            ┆ DEVICES   ┆         ┆ 2017,     ┆   ┆           ┆           ┆           ┆           │
│            ┆ INC       ┆         ┆ 2018,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2019, …   ┆   ┆           ┆           ┆           ┆           │
│ 0000003197 ┆ CECO ENVI ┆ 6       ┆ 2015,     ┆ … ┆ 8996      ┆ 10        ┆ 1499.3333 ┆ 1.666667  │
│            ┆ RONMENTAL ┆         ┆ 2016,     ┆   ┆           ┆           ┆ 33        ┆           │
│            ┆ CORP      ┆         ┆ 2017,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2018,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2019, …   ┆   ┆           ┆           ┆           ┆           │
│ 0000001800 ┆ ABBOTT    ┆ 6       ┆ 2015,     ┆ … ┆ 8795      ┆ 10        ┆ 1465.8333 ┆ 1.666667  │
│            ┆ LABORATOR ┆         ┆ 2016,     ┆   ┆           ┆           ┆ 33        ┆           │
│            ┆ IES       ┆         ┆ 2017,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2018,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2019, …   ┆   ┆           ┆           ┆           ┆           │
│ 0000001750 ┆ AAR CORP  ┆ 6       ┆ 2015,     ┆ … ┆ 6573      ┆ 10        ┆ 1095.5    ┆ 1.666667  │
│            ┆           ┆         ┆ 2016,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2017,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2018,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2019, …   ┆   ┆           ┆           ┆           ┆           │
│ 0000002186 ┆ BK Techno ┆ 6       ┆ 2015,     ┆ … ┆ 5726      ┆ 10        ┆ 954.33333 ┆ 1.666667  │
│            ┆ logies    ┆         ┆ 2016,     ┆   ┆           ┆           ┆ 3         ┆           │
│            ┆ Corp      ┆         ┆ 2017,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2018,     ┆   ┆           ┆           ┆           ┆           │
│            ┆           ┆         ┆ 2019, …   ┆   ┆           ┆           ┆           ┆           │
│ 0000002178 ┆ ADAMS     ┆ 6       ┆ 2015,     ┆ … ┆ 4925      ┆ 8         ┆ 820.83333 ┆ 1.333333  │
│            ┆ RESOURCES ┆         ┆ 2016,     ┆   ┆           ┆           ┆ 3         ┆           │
│            ┆ & ENERGY, ┆         ┆ 2017,   

In [20]:
# --- 2a) document table (one row per docID) ---
docs = (
    df_year
    .group_by("docID")
    .agg([
        pl.first("cik").alias("cik"),
        pl.first("name").alias("name"),
        pl.first("fiscal_year").alias("fiscal_year"),
        pl.n_unique("section").alias("n_sections_doc"),
        pl.count().alias("n_sentences_doc"),
        # flatten returns (1d/5d/30d)
        pl.col("returns").struct.field("1d").struct.field("ret").first().alias("ret_1d"),
        pl.col("returns").struct.field("5d").struct.field("ret").first().alias("ret_5d"),
        pl.col("returns").struct.field("30d").struct.field("ret").first().alias("ret_30d"),
    ])
)

docs.head(20)

C:\Users\joems\AppData\Local\Temp\ipykernel_26476\1167462977.py:10: DeprecationWarning: `pl.count()` is deprecated. Please use `pl.len()` instead.
(Deprecated in version 0.20.5)
  pl.count().alias("n_sentences_doc"),


shape: (20, 9)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ docID     ┆ cik       ┆ name      ┆ fiscal_ye ┆ … ┆ n_sentenc ┆ ret_1d    ┆ ret_5d    ┆ ret_30d  │
│ ---       ┆ ---       ┆ ---       ┆ ar        ┆   ┆ es_doc    ┆ ---       ┆ ---       ┆ ---      │
│ str       ┆ str       ┆ str       ┆ ---       ┆   ┆ ---       ┆ f64       ┆ f64       ┆ f64      │
│           ┆           ┆           ┆ i32       ┆   ┆ u32       ┆           ┆           ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 000000296 ┆ 000000296 ┆ Air       ┆ 2013      ┆ … ┆ 1814      ┆ -0.005468 ┆ -0.018502 ┆ 0.03591  │
│ 9_10-K_20 ┆ 9         ┆ Products  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 13        ┆           ┆ & Chemica ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ ls, Inc.  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000296 ┆ 000000296 ┆ Air       ┆ 2014      ┆ … ┆ 1871      ┆ 0.001378  ┆ -0.007303 ┆ 0.023631 │
│ 9_10-K_20 ┆ 9         ┆ Products  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 14        ┆           ┆ & Chemica ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ ls, Inc.  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2009      ┆ … ┆ 1056      ┆ 0.008914  ┆ 0.010585  ┆ 0.040669 │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 09        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000217 ┆ 000000217 ┆ ADAMS     ┆ 2006      ┆ … ┆ 752       ┆ -0.034113 ┆ -0.00747  ┆ -0.06499 │
│ 8_10-K_20 ┆ 8         ┆ RESOURCES ┆           ┆   ┆           ┆           ┆           ┆          │
│ 06        ┆           ┆ & ENERGY, ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ INC.      ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000196 ┆ 000000196 ┆ WORLDS    ┆ 2016      ┆ … ┆ 649       ┆ 0.0       ┆ 0.0       ┆ 0.0      │
│ 1_10-K_20 ┆ 1         ┆ INC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 16        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2011      ┆ … ┆ 940       ┆ 0.022313  ┆ 0.010142  ┆ -0.19682 │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 4        │
│ 11        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000296 ┆ 000000296 ┆ Air       ┆ 2002      ┆ … ┆ 455       ┆ 0.023619  ┆ -0.027057 ┆ 0.00935  │
│ 9_10-K_20 ┆ 9         ┆ Products  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 02        ┆           ┆ & Chemica ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ ls, Inc.  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000218 ┆ 000000218 ┆ BK Techno ┆ 2004      ┆ … ┆ 927       ┆ -0.020408 ┆ -0.044898 ┆ -0.05306 │
│ 6_10-K_20 ┆ 6         ┆ logies    ┆           ┆   ┆           ┆           ┆           ┆ 1        │
│ 04        ┆           ┆ Corp      ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000248 ┆ 000000248 ┆ ADVANCED  ┆ 2006      ┆ … ┆ 2790      ┆ -0.059058 ┆ -0.06503  ┆ -0.14864 │
│ 8_10-K_20 ┆ 8         ┆ MICRO     ┆           ┆   ┆           ┆           ┆           ┆          │
│ 06        ┆           ┆ DEVICES   ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ INC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000248 ┆ 000000248 ┆ ADVANCED  ┆ 2009    

In [21]:


# --- 2b) company × fiscal_year summary ---
company_year = (
    docs
    .group_by(["cik","name","fiscal_year"])
    .agg([
        pl.n_unique("docID").alias("n_docs"),
        pl.sum("n_sentences_doc").alias("n_sentences"),
        pl.mean("n_sections_doc").alias("avg_sections_per_doc"),
        # market-reaction snapshot (means across docs in that year)
        pl.mean("ret_1d").alias("avg_ret_1d"),
        pl.mean("ret_5d").alias("avg_ret_5d"),
        pl.mean("ret_30d").alias("avg_ret_30d"),
    ])
    .sort(["cik","fiscal_year"])
)

company_year.head(20)


shape: (20, 9)
┌────────────┬──────────┬────────────┬────────┬───┬────────────┬───────────┬───────────┬───────────┐
│ cik        ┆ name     ┆ fiscal_yea ┆ n_docs ┆ … ┆ avg_sectio ┆ avg_ret_1 ┆ avg_ret_5 ┆ avg_ret_3 │
│ ---        ┆ ---      ┆ r          ┆ ---    ┆   ┆ ns_per_doc ┆ d         ┆ d         ┆ 0d        │
│ str        ┆ str      ┆ ---        ┆ u32    ┆   ┆ ---        ┆ ---       ┆ ---       ┆ ---       │
│            ┆          ┆ i32        ┆        ┆   ┆ f64        ┆ f64       ┆ f64       ┆ f64       │
╞════════════╪══════════╪════════════╪════════╪═══╪════════════╪═══════════╪═══════════╪═══════════╡
│ 0000001750 ┆ AAR CORP ┆ 1994       ┆ 1      ┆ … ┆ 14.0       ┆ 0.0       ┆ -0.018018 ┆ -0.072072 │
│ 0000001750 ┆ AAR CORP ┆ 1995       ┆ 1      ┆ … ┆ 14.0       ┆ 0.030303  ┆ 0.015151  ┆ 0.121212  │
│ 0000001750 ┆ AAR CORP ┆ 2002       ┆ 1      ┆ … ┆ 15.0       ┆ -0.007728 ┆ -0.080371 ┆ -0.31221  │
│ 0000001750 ┆ AAR CORP ┆ 2003       ┆ 1      ┆ … ┆ 16.0       ┆ 0.158273  ┆ 0.122302  ┆ 0.330935  │
│ 0000001750 ┆ AAR CORP ┆ 2004       ┆ 1      ┆ … ┆ 17.0       ┆ -0.06037  ┆ -0.055501 ┆ -0.016553 │
│ …          ┆ …        ┆ …          ┆ …      ┆ … ┆ …          ┆ …         ┆ …         ┆ …         │
│ 0000001750 ┆ AAR CORP ┆ 2015       ┆ 1      ┆ … ┆ 20.0       ┆ -0.05463  ┆ -0.081173 ┆ -0.175305 │
│ 0000001750 ┆ AAR CORP ┆ 2016       ┆ 1      ┆ … ┆ 20.0       ┆ -0.081869 ┆ -0.03115  ┆ -0.052576 │
│ 0000001750 ┆ AAR CORP ┆ 2017       ┆ 1      ┆ … ┆ 20.0       ┆ 0.027012  ┆ 0.006821  ┆ -0.032928 │
│ 0000001750 ┆ AAR CORP ┆ 2018       ┆ 1      ┆ … ┆ 20.0       ┆ -0.100927 ┆ -0.066941 ┆ -0.050178 │
│ 0000001750 ┆ AAR CORP ┆ 2019       ┆ 1      ┆ … ┆ 20.0       ┆ 0.011395  ┆ -0.00108  ┆ 0.017152  │
└────────────┴──────────┴────────────┴────────┴───┴────────────┴───────────┴───────────┴───────────┘

### Resuming practice; Lazy conversion & predicate/pushdown, Docs table and flattening, Window functions & reshape.


    Lab A: You can explain why filtering before groupby makes counts correct and show pushdown in .explain().
    Lab B: You can justify document-grain flattening and prove no double-counting with the checks.
    Lab C: You can demo a window calculation and a melt into tidy long form, with sanity invariants.

In [26]:

# Load dataset
DATA_PATH = Path("../data/exports/sec_filings_small_full.parquet")
df = pl.read_parquet(DATA_PATH)

print(f"Dataset loaded: {df.shape[0]:,} rows × {df.shape[1]} columns")
print(f"Memory usage: {df.estimated_size('mb'):.1f} MB")

lf = pl.scan_parquet(DATA_PATH)  # lazy

# print("LazyFrame schema:", lf.schema)
# print("Memory usage of lf is:", lf.estimated_size('mb'))

Dataset loaded: 200,000 rows × 19 columns
Memory usage: 144.1 MB


In [ ]:
## strptime : converts string to datetime.

lf = lf.with_columns(
    pl.col("reportDate").str.strptime(pl.Date, strict=False).dt.year().alias("fiscal_year")
)

KPI_CORE = [10, 8, 9, 0, 1]  # Notes, MD&A, FS, Business, Risk
lf = lf.filter( (pl.col("fiscal_year") > 2015) & (pl.col("section").is_in(KPI_CORE)) )

lf_roll = lf.select(["cik","name","fiscal_year","docID","section","sentenceID"])

lf_roll = (lf_roll
    .group_by(["cik","name"])
    .agg(
        pl.n_unique("fiscal_year").alias("n_years"),
        pl.col("fiscal_year").unique().sort().alias("years_arr"),

        pl.n_unique("docID").alias("n_docs_filings"),
        pl.col("docID").unique().sort().alias("docID_arr"),
        
        pl.len().alias("row_count"),
        pl.n_unique("section").alias("n_sections"),
        pl.col("sentenceID").n_unique().alias("n_sentences"),
    )
)


print(lf_roll.explain())      # should show predicate & projection pushdown
company_rollup = lf_roll.collect()

# .explain() mentions predicate pushdown and lists only needed columns.
# company_rollup.height equals number of companies in the filtered slice.

print("company_rollup:", company_rollup.head(10))
print("\n=================================================\n")




AGGREGATE[maintain_order: false]
  [col("fiscal_year").n_unique().alias("n_years"), col("fiscal_year").unique().sort(asc).alias("years_arr"), col("docID").n_unique().alias("n_docs_filings"), col("docID").unique().sort(asc).alias("docID_arr"), len().alias("row_count"), col("section").n_unique().alias("n_sections"), col("sentenceID").n_unique().alias("n_sentences")] BY [col("cik"), col("name")]
  FROM
  simple π 6/6 ["cik", "name", "fiscal_year", ... 3 other columns]
    FILTER [(col("section").is_in([[10, 8, … 1]])) & ([(col("fiscal_year")) > (2015)])]
    FROM
       WITH_COLUMNS:
       [col("reportDate").str.strptime(["raise"]).dt.year().alias("fiscal_year")] 
        FILTER [([(col("fiscal_year")) > (2015)]) & (col("section").is_in([[10, 8, … 1]]))]
        FROM
           WITH_COLUMNS:
           [col("reportDate").str.strptime(["raise"]).dt.year().alias("fiscal_year")] 
            FILTER [([(col("fiscal_year")) > (2015)]) & (col("section").is_in([[10, 8, … 1]]))]
            FROM

In [ ]:
## Preview, list join again as strings. 

# Show a tiny head without materializing everything
preview = lf_roll.limit(10).collect()         
print(preview)

print("\n=================================================\n")

rollup_with_views = (
    lf_roll
    .with_columns(
        years_view = pl.col("years_arr").list.eval(pl.element().cast(pl.Utf8)).list.join(", "),
        docIDs_view = pl.col("docID_arr").list.eval(pl.element().cast(pl.Utf8)).list.join(", ")
    )
    .select("cik","name","n_years","years_arr","years_view",
            "n_docs_filings","docID_arr","docIDs_view","n_sentences","n_sections")
)


rollup_with_views.collect().head(10)



shape: (10, 9)
┌────────────┬───────────┬─────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ cik        ┆ name      ┆ n_years ┆ years_arr ┆ … ┆ docID_arr ┆ row_count ┆ n_section ┆ n_sentenc │
│ ---        ┆ ---       ┆ ---     ┆ ---       ┆   ┆ ---       ┆ ---       ┆ s         ┆ es        │
│ str        ┆ str       ┆ u32     ┆ list[i32] ┆   ┆ list[str] ┆ u32       ┆ ---       ┆ ---       │
│            ┆           ┆         ┆           ┆   ┆           ┆           ┆ u32       ┆ u32       │
╞════════════╪═══════════╪═════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 0000003197 ┆ CECO ENVI ┆ 5       ┆ [2016,    ┆ … ┆ ["0000003 ┆ 4392      ┆ 5         ┆ 4392      │
│            ┆ RONMENTAL ┆         ┆ 2017, …   ┆   ┆ 197_10-K_ ┆           ┆           ┆           │
│            ┆ CORP      ┆         ┆ 2020]     ┆   ┆ 2016",    ┆           ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆           ┆

shape: (10, 10)
┌────────────┬───────────┬─────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ cik        ┆ name      ┆ n_years ┆ years_arr ┆ … ┆ docID_arr ┆ docIDs_vi ┆ n_sentenc ┆ n_section │
│ ---        ┆ ---       ┆ ---     ┆ ---       ┆   ┆ ---       ┆ ew        ┆ es        ┆ s         │
│ str        ┆ str       ┆ u32     ┆ list[i32] ┆   ┆ list[str] ┆ ---       ┆ ---       ┆ ---       │
│            ┆           ┆         ┆           ┆   ┆           ┆ str       ┆ u32       ┆ u32       │
╞════════════╪═══════════╪═════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 0000002178 ┆ ADAMS     ┆ 5       ┆ [2016,    ┆ … ┆ ["0000002 ┆ 000000217 ┆ 4021      ┆ 4         │
│            ┆ RESOURCES ┆         ┆ 2017, …   ┆   ┆ 178_10-K_ ┆ 8_10-K_20 ┆           ┆           │
│            ┆ & ENERGY, ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆ INC.      ┆         ┆           ┆   ┆ "0000…    ┆ 00000021… ┆           ┆           │
│ 0000002098 ┆ ACME      ┆ 5       ┆ [2016,    ┆ … ┆ ["0000002 ┆ 000000209 ┆ 3616      ┆ 5         │
│            ┆ UNITED    ┆         ┆ 2017, …   ┆   ┆ 098_10-K_ ┆ 8_10-K_20 ┆           ┆           │
│            ┆ CORP      ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆ 00000020… ┆           ┆           │
│ 0000003197 ┆ CECO ENVI ┆ 5       ┆ [2016,    ┆ … ┆ ["0000003 ┆ 000000319 ┆ 4392      ┆ 5         │
│            ┆ RONMENTAL ┆         ┆ 2017, …   ┆   ┆ 197_10-K_ ┆ 7_10-K_20 ┆           ┆           │
│            ┆ CORP      ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆ 00000031… ┆           ┆           │
│ 0000002969 ┆ Air       ┆ 5       ┆ [2016,    ┆ … ┆ ["0000002 ┆ 000000296 ┆ 9277      ┆ 5         │
│            ┆ Products  ┆         ┆ 2017, …   ┆   ┆ 969_10-K_ ┆ 9_10-K_20 ┆           ┆           │
│            ┆ & Chemica ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆ ls, Inc.  ┆         ┆           ┆   ┆ "0000…    ┆ 00000029… ┆           ┆           │
│ 0000001800 ┆ ABBOTT    ┆ 5       ┆ [2016,    ┆ … ┆ ["0000001 ┆ 000000180 ┆ 6508      ┆ 5         │
│            ┆ LABORATOR ┆         ┆ 2017, …   ┆   ┆ 800_10-K_ ┆ 0_10-K_20 ┆           ┆           │
│            ┆ IES       ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆ 00000018… ┆           ┆           │
│ 0000002186 ┆ BK Techno ┆ 5       ┆ [2016,    ┆ … ┆ ["0000002 ┆ 000000218 ┆ 4655      ┆ 5         │
│            ┆ logies    ┆         ┆ 2017, …   ┆   ┆ 186_10-K_ ┆ 6_10-K_20 ┆           ┆           │
│            ┆ Corp      ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆ 00000021… ┆           ┆           │
│ 0000003453 ┆ Matson,   ┆ 2       ┆ [2019,    ┆ … ┆ ["0000003 ┆ 000000345 ┆ 1273      ┆ 5         │
│            ┆ Inc.      ┆         ┆ 2020]     ┆   ┆ 453_10-K_ ┆ 3_10-K_20 ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ 2019",    ┆ 19,       ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆ 00000034… ┆           ┆           │
│ 0000001750 ┆ AAR CORP  ┆ 5       ┆ [2016,    ┆ … ┆ ["0000001 ┆ 000000175 ┆ 4901      ┆ 5         │
│            ┆           ┆         ┆ 2017, …   ┆   ┆ 750_10-K_ ┆ 0_10-K_20 ┆           ┆           │
│            ┆           ┆         ┆ 2020]     ┆   ┆ 2016",    ┆ 16,       ┆           ┆           │
│            ┆           ┆         ┆           ┆   ┆ "0000…    ┆ 00000017… ┆           ┆           │
│ 0000002488 ┆ ADVANCED  ┆ 5       ┆ [2016,    ┆ … ┆ ["0000002 ┆ 000000248 ┆ 6977      ┆ 5         │
│            ┆ MICRO     ┆         ┆ 2017, … 

In [52]:
## LAB 2 Practice: Caching LazyFrames
# After you define `lf` with year + section filters:

# 0) Build the base lazy slice ONCE (derive year + filter). Do NOT aggregate here.
lf_base = (
    pl.scan_parquet(DATA_PATH)
    .with_columns(
        pl.col("reportDate").str.strptime(pl.Date, strict=False).dt.year().alias("fiscal_year")
    )
    .filter(
        (pl.col("fiscal_year") > 2015) &
        (pl.col("section").is_in([10, 8, 9, 0, 1]))
    )
)

lf_cached = lf_base.cache()

# 2) Build your aggregations from the cached slice
company_rollup_lazy = (
    lf_cached
    .group_by(["cik","name"])
    .agg(
        n_years = pl.n_unique("fiscal_year"),
        years_arr = pl.col("fiscal_year").unique().sort(),
        n_docs_filings = pl.n_unique("docID"),
        docID_arr = pl.col("docID").unique().sort(),
        n_sentences = pl.len(),
        n_sections  = pl.n_unique("section"),
    )
)

section_rollup_lazy = (
    lf_cached
    .group_by("section")
    .agg(
        n_sentences = pl.len(),
        n_docs = pl.n_unique("docID"),
    )
    .sort("n_sentences", descending=True)
)


company_rollup = company_rollup_lazy.limit(10).collect()
section_rollup  = section_rollup_lazy.limit(10).collect()

company_rollup
# section_rollup

shape: (10, 8)
┌────────────┬────────────┬─────────┬────────────┬────────────┬────────────┬───────────┬───────────┐
│ cik        ┆ name       ┆ n_years ┆ years_arr  ┆ n_docs_fil ┆ docID_arr  ┆ n_sentenc ┆ n_section │
│ ---        ┆ ---        ┆ ---     ┆ ---        ┆ ings       ┆ ---        ┆ es        ┆ s         │
│ str        ┆ str        ┆ u32     ┆ list[i32]  ┆ ---        ┆ list[str]  ┆ ---       ┆ ---       │
│            ┆            ┆         ┆            ┆ u32        ┆            ┆ u32       ┆ u32       │
╞════════════╪════════════╪═════════╪════════════╪════════════╪════════════╪═══════════╪═══════════╡
│ 0000003453 ┆ Matson,    ┆ 2       ┆ [2019,     ┆ 2          ┆ ["00000034 ┆ 1273      ┆ 5         │
│            ┆ Inc.       ┆         ┆ 2020]      ┆            ┆ 53_10-K_20 ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ 19",       ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000001750 ┆ AAR CORP   ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000017 ┆ 4901      ┆ 5         │
│            ┆            ┆         ┆ 2017, …    ┆            ┆ 50_10-K_20 ┆           ┆           │
│            ┆            ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000002488 ┆ ADVANCED   ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000024 ┆ 6977      ┆ 5         │
│            ┆ MICRO      ┆         ┆ 2017, …    ┆            ┆ 88_10-K_20 ┆           ┆           │
│            ┆ DEVICES    ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆ INC        ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000001800 ┆ ABBOTT LAB ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000018 ┆ 6508      ┆ 5         │
│            ┆ ORATORIES  ┆         ┆ 2017, …    ┆            ┆ 00_10-K_20 ┆           ┆           │
│            ┆            ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000002186 ┆ BK Technol ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000021 ┆ 4655      ┆ 5         │
│            ┆ ogies Corp ┆         ┆ 2017, …    ┆            ┆ 86_10-K_20 ┆           ┆           │
│            ┆            ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000002098 ┆ ACME       ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000020 ┆ 3616      ┆ 5         │
│            ┆ UNITED     ┆         ┆ 2017, …    ┆            ┆ 98_10-K_20 ┆           ┆           │
│            ┆ CORP       ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000001961 ┆ WORLDS INC ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000019 ┆ 1710      ┆ 4         │
│            ┆            ┆         ┆ 2017, …    ┆            ┆ 61_10-K_20 ┆           ┆           │
│            ┆            ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆            ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000002178 ┆ ADAMS      ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000021 ┆ 4021      ┆ 4         │
│            ┆ RESOURCES  ┆         ┆ 2017, …    ┆            ┆ 78_10-K_20 ┆           ┆           │
│            ┆ & ENERGY,  ┆         ┆ 2020]      ┆            ┆ 16",       ┆           ┆           │
│            ┆ INC.       ┆         ┆            ┆            ┆ "0000…     ┆           ┆           │
│ 0000002969 ┆ Air        ┆ 5       ┆ [2016,     ┆ 5          ┆ ["00000029 ┆ 9277      ┆ 5         │
│            ┆ Products & ┆         ┆ 2017, … 

In [ ]:
# Goal: create a one-row-per-docID table to attach document-level fields safely (returns, later labels), then a company×year summary.

# Steps
# Start from the same filtered lazy frame (lf) from Lab A.
# Build docs (one row per filing)

# 0) Build the base lazy slice ONCE (derive year + filter). Do NOT aggregate here.
lf_base = (
    pl.scan_parquet(DATA_PATH)
    .with_columns(
        pl.col("reportDate").str.strptime(pl.Date, strict=False).dt.year().alias("fiscal_year")
    )
    .filter(
        (pl.col("fiscal_year") > 2015) &
        (pl.col("section").is_in([10, 8, 9, 0, 1]))
    )
)

docs = (
    lf
    .group_by("docID")
    .agg(
        pl.first("cik").alias("cik"),
        pl.first("name").alias("name"),
        pl.first("fiscal_year").alias("fiscal_year"),
        pl.n_unique("section").alias("n_sections_doc"),
        pl.len().alias("n_sentences_doc"),
        # flatten returns (1d/5d/30d) *once* at the doc grain
        pl.col("returns").struct.field("1d").struct.field("ret").first().alias("ret_1d"),
        pl.col("returns").struct.field("5d").struct.field("ret").first().alias("ret_5d"),
        pl.col("returns").struct.field("30d").struct.field("ret").first().alias("ret_30d"),
    )
)

docs_df = docs.collect()
docs_df.head(5)

shape: (5, 9)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ docID     ┆ cik       ┆ name      ┆ fiscal_ye ┆ … ┆ n_sentenc ┆ ret_1d    ┆ ret_5d    ┆ ret_30d  │
│ ---       ┆ ---       ┆ ---       ┆ ar        ┆   ┆ es_doc    ┆ ---       ┆ ---       ┆ ---      │
│ str       ┆ str       ┆ str       ┆ ---       ┆   ┆ ---       ┆ f64       ┆ f64       ┆ f64      │
│           ┆           ┆           ┆ i32       ┆   ┆ u32       ┆           ┆           ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 000000180 ┆ 000000180 ┆ ABBOTT    ┆ 2019      ┆ … ┆ 1348      ┆ -0.043296 ┆ -0.080262 ┆ -0.28984 │
│ 0_10-K_20 ┆ 0         ┆ LABORATOR ┆           ┆   ┆           ┆           ┆           ┆ 9        │
│ 19        ┆           ┆ IES       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000296 ┆ 000000296 ┆ Air       ┆ 2017      ┆ … ┆ 1928      ┆ 0.004476  ┆ 0.00889   ┆ 0.007957 │
│ 9_10-K_20 ┆ 9         ┆ Products  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 17        ┆           ┆ & Chemica ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ ls, Inc.  ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000248 ┆ 000000248 ┆ ADVANCED  ┆ 2019      ┆ … ┆ 779       ┆ 0.037901  ┆ 0.088296  ┆ 0.001874 │
│ 8_10-K_20 ┆ 8         ┆ MICRO     ┆           ┆   ┆           ┆           ┆           ┆          │
│ 19        ┆           ┆ DEVICES   ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ INC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000218 ┆ 000000218 ┆ BK Techno ┆ 2017      ┆ … ┆ 883       ┆ -0.027397 ┆ 0.013699  ┆ 0.093137 │
│ 6_10-K_20 ┆ 6         ┆ logies    ┆           ┆   ┆           ┆           ┆           ┆          │
│ 17        ┆           ┆ Corp      ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2018      ┆ … ┆ 927       ┆ -0.100927 ┆ -0.066941 ┆ -0.05017 │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 8        │
│ 18        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

### Next 4 cells are chained-practice items across complex ideas, caching, lazy and more.

In [73]:
## flatten → unpivot → aggregate on a LazyFrame. end-to-end query that does it correctly for finance.
## PART 1

"""
Document grain first (avoid double counting): 1 row per docID, flatten returns.{1d,5d,30d}.ret.
Unpivot those returns to long form (horizon ∈ {ret_1d, ret_5d, ret_30d}, ret value).
Aggregate per (cik, name, fiscal_year, horizon) using mean/median and compounded return
"""

## base lazy frame, with year + section filters:
lf_base = (
    pl.scan_parquet(DATA_PATH)
    .with_columns(
        pl.col("reportDate").str.strptime(pl.Date, strict=False).dt.year().alias("fiscal_year")
    )
    .filter(
        (pl.col("fiscal_year") > 2015) &
        (pl.col("section").is_in([10, 8, 9, 0, 1]))
    )
)

### -- bad idea:
# # first, concat all tickers in a doc. 
# tickers_arr_expr = pl.concat_list("tickers").list.unique().list.sort()

lf_norm = lf_base.with_columns(
    tickers_norm = (
        pl.col("tickers")
          .list.eval(pl.element().str.to_uppercase())  # normalize
          .list.unique().list.sort()
    ),
    exchanges_norm = pl.col("exchanges").list.unique().list.sort()
)


## gropuping and multi agg; as per document docID level.

lf_docs =  ( 
    lf_norm.group_by("docID")
    .agg(
        cik = pl.first("cik"),
        cik_un = pl.col("cik").n_unique(),

        name_first = pl.first("name"),
        name_nu = pl.col("name").n_unique(),
        name_mode = pl.col("name").mode().first(),    # true mode drops an entire list.

        fiscal_year = pl.first("fiscal_year"),
        fiscal_year_un = pl.col("fiscal_year").n_unique(),

        n_sections_doc = pl.n_unique("section"),
        n_sentences_doc = pl.len(),
        sections_arr = pl.col("section").unique().sort(),

        # ticker list: first non-null normalized list
        tickers_arr    = pl.col("tickers_norm").drop_nulls().first(),
        tickers_arr_nu = pl.col("tickers_norm").drop_nulls().n_unique(),  # expect == 1
        # primary ticker: deterministic pick from the list
        ticker_primary = pl.col("tickers_norm").drop_nulls().first().list.first(),


        ret_1d           = pl.col("returns").struct.field("1d").struct.field("ret").first(),
        ret_1d_nu        = pl.col("returns").struct.field("1d").struct.field("ret").n_unique(),
        ret_5d           = pl.col("returns").struct.field("5d").struct.field("ret").first(),
        ret_5d_nu        = pl.col("returns").struct.field("5d").struct.field("ret").n_unique(),
        ret_30d          = pl.col("returns").struct.field("30d").struct.field("ret").first(),
        ret_30d_nu       = pl.col("returns").struct.field("30d").struct.field("ret").n_unique(),
    )

    .with_columns(
        name = pl.when(pl.col("name_nu") == 1).then(pl.col("name_first"))
                 .otherwise(pl.coalesce([pl.col("name_mode"), pl.col("name_first")])),
        # tickers_arr = pl.col("tickers_concat").list.unique().sort(),         # then, unique + sort. dedupe and sort.
    )
    .with_columns(
        # has been written better above.
        # ticker_primary = pl.col("tickers_arr").list.first(), 
        qa_alert = ( (pl.col("cik_un") > 1) | (pl.col("name_nu") > 1) | (pl.col("fiscal_year_un") > 1) | 
                    (pl.col("ret_1d_nu") > 1) | (pl.col("ret_5d_nu") > 1) | (pl.col("ret_30d_nu") > 1) )
    )
    .select(
        "docID","cik","name","ticker_primary","tickers_arr",
        "fiscal_year","n_sentences_doc","n_sections_doc","sections_arr",
        "ret_1d","ret_5d","ret_30d","qa_alert",
        # QA counters if you want --- !
        # "cik_un","name_nu","fiscal_year_un","ret_1d_nu","ret_5d_nu","ret_30d_nu",
        "tickers_arr_nu" 
    )
)


## sanity.
print(lf_docs.explain())

limitval = 30
     
docs_sample = lf_docs.limit(limitval).collect()
bad_docs = lf_docs.filter(pl.col("qa_alert")).limit(limitval).collect()

print("\nSample docs:", docs_sample.shape, "| QA-flagged:", bad_docs.shape)

print(lf_docs.explain(optimized=True))

print("\n=================================================\n")

"""
On a LazyFrame, methods like .head()/.limit() return another LazyFrame (a sliced plan), not data.
When you “print” or display a LazyFrame in the notebook, Polars shows its query plan (what will run), not the materialized table.
"""

lf_docs.limit(limitval).collect() 

# keep only columns needed, and unpivot - to tidy long form. 
# aggregate per company × year × horizon


simple π 14/14 ["docID", "cik", "name", ... 11 other columns]
   WITH_COLUMNS:
   [when([(col("name_nu")) == (1)]).then(col("name_first")).otherwise(col("name_mode").coalesce([col("name_first")])).alias("name"), [([([([([([(col("cik_un")) > (1)]) | ([(col("name_nu")) > (1)])]) | ([(col("fiscal_year_un")) > (1)])]) | ([(col("ret_1d_nu")) > (1)])]) | ([(col("ret_5d_nu")) > (1)])]) | ([(col("ret_30d_nu")) > (1)])].alias("qa_alert")] 
    AGGREGATE[maintain_order: false]
      [col("cik").first(), col("cik").n_unique().alias("cik_un"), col("name").first().alias("name_first"), col("name").n_unique().alias("name_nu"), col("name").mode().first().alias("name_mode"), col("fiscal_year").first(), col("fiscal_year").n_unique().alias("fiscal_year_un"), col("section").n_unique().alias("n_sections_doc"), len().alias("n_sentences_doc"), col("section").unique().sort(asc).alias("sections_arr"), col("tickers_norm").drop_nulls().first().alias("tickers_arr"), col("tickers_norm").drop_nulls().n_unique().ali

shape: (30, 14)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬──────────┬───────────┐
│ docID     ┆ cik       ┆ name      ┆ ticker_pr ┆ … ┆ ret_5d    ┆ ret_30d   ┆ qa_alert ┆ tickers_a │
│ ---       ┆ ---       ┆ ---       ┆ imary     ┆   ┆ ---       ┆ ---       ┆ ---      ┆ rr_nu     │
│ str       ┆ str       ┆ str       ┆ ---       ┆   ┆ f64       ┆ f64       ┆ bool     ┆ ---       │
│           ┆           ┆           ┆ str       ┆   ┆           ┆           ┆          ┆ u32       │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪══════════╪═══════════╡
│ 000000217 ┆ 000000217 ┆ ADAMS     ┆ AE        ┆ … ┆ -0.047431 ┆ 0.063241  ┆ false    ┆ 1         │
│ 8_10-K_20 ┆ 8         ┆ RESOURCES ┆           ┆   ┆           ┆           ┆          ┆           │
│ 17        ┆           ┆ & ENERGY, ┆           ┆   ┆           ┆           ┆          ┆           │
│           ┆           ┆ INC.      ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000248 ┆ 000000248 ┆ ADVANCED  ┆ AMD       ┆ … ┆ 0.088296  ┆ 0.001874  ┆ false    ┆ 1         │
│ 8_10-K_20 ┆ 8         ┆ MICRO     ┆           ┆   ┆           ┆           ┆          ┆           │
│ 19        ┆           ┆ DEVICES   ┆           ┆   ┆           ┆           ┆          ┆           │
│           ┆           ┆ INC       ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ AIR       ┆ … ┆ -0.066941 ┆ -0.050178 ┆ false    ┆ 1         │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆          ┆           │
│ 18        ┆           ┆           ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000217 ┆ 000000217 ┆ ADAMS     ┆ AE        ┆ … ┆ -0.023803 ┆ 0.091028  ┆ false    ┆ 1         │
│ 8_10-K_20 ┆ 8         ┆ RESOURCES ┆           ┆   ┆           ┆           ┆          ┆           │
│ 16        ┆           ┆ & ENERGY, ┆           ┆   ┆           ┆           ┆          ┆           │
│           ┆           ┆ INC.      ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ AIR       ┆ … ┆ -0.03115  ┆ -0.052576 ┆ false    ┆ 1         │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆          ┆           │
│ 16        ┆           ┆           ┆           ┆   ┆           ┆           ┆          ┆           │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …        ┆ …         │
│ 000000196 ┆ 000000196 ┆ WORLDS    ┆ WDDD      ┆ … ┆ 0.045455  ┆ 0.045455  ┆ false    ┆ 1         │
│ 1_10-K_20 ┆ 1         ┆ INC       ┆           ┆   ┆           ┆           ┆          ┆           │
│ 19        ┆           ┆           ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000218 ┆ 000000218 ┆ BK Techno ┆ BKTI      ┆ … ┆ 0.09396   ┆ 0.111857  ┆ false    ┆ 1         │
│ 6_10-K_20 ┆ 6         ┆ logies    ┆           ┆   ┆           ┆           ┆          ┆           │
│ 20        ┆           ┆ Corp      ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000296 ┆ 000000296 ┆ Air       ┆ APD       ┆ … ┆ 0.00889   ┆ 0.007957  ┆ false    ┆ 1         │
│ 9_10-K_20 ┆ 9         ┆ Products  ┆           ┆   ┆           ┆           ┆          ┆           │
│ 17        ┆           ┆ & Chemica ┆           ┆   ┆           ┆           ┆          ┆           │
│           ┆           ┆ ls, Inc.  ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000196 ┆ 000000196 ┆ WORLDS    ┆ WDDD      ┆ … ┆ 0.02381   ┆ 0.071429  ┆ false    ┆ 1         │
│ 1_10-K_20 ┆ 1         ┆ INC       ┆           ┆   ┆           ┆           ┆          ┆           │
│ 20        ┆           ┆           ┆           ┆   ┆           ┆           ┆          ┆           │
│ 000000209 ┆ 000000209 ┆ ACME      ┆ ACU       ┆ … ┆ 0.061439  ┆ 0.125837  ┆ false    ┆ 1         │
│ 8_10-K_20 ┆ 8         ┆ UNITED    ┆        

In [ ]:
## RESUMING with the same lf_docs, we want to do more now. 

# 1) Unpivot to tidy long form (lazy)

lf_doc_meta = lf_docs.select(
    "docID","ticker_primary","n_sentences_doc","n_sections_doc","sections_arr"
)


lf_doc_returns_long = (
    lf_docs
    .select("docID", "cik", "name", "fiscal_year", 
            "ticker_primary", "n_sentences_doc","n_sections_doc","sections_arr", 
            "ret_1d", "ret_5d", "ret_30d")
    .unpivot(
        index=["docID", "cik", "name", "fiscal_year"],   # formerly id_vars
        on=["ret_1d", "ret_5d", "ret_30d"],              # formerly value_vars
        variable_name="horizon",
        value_name="ret"
    )
    .filter(pl.col("ret").is_not_null())
    .with_columns(
        # 'ret_1d' -> '1d', etc. 
        horizon = pl.col("horizon").str.replace("^ret_", "", literal=False),
        # guard for compounding (avoid log(<=0))
        ret_safe = pl.col("ret").clip(lower_bound=-0.9999)
        # if lacks Expr.clip(), fallback:
        # ret_safe = pl.when(pl.col("ret") < -0.9999).then(-0.9999).otherwise(pl.col("ret"))
    )
    # bring the doc-level meta back
    .join(lf_doc_meta, on="docID", how="left")
)

lf_doc_returns_long.limit(limitval).collect()




shape: (30, 11)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ docID     ┆ cik       ┆ name      ┆ fiscal_ye ┆ … ┆ ticker_pr ┆ n_sentenc ┆ n_section ┆ sections │
│ ---       ┆ ---       ┆ ---       ┆ ar        ┆   ┆ imary     ┆ es_doc    ┆ s_doc     ┆ _arr     │
│ str       ┆ str       ┆ str       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│           ┆           ┆           ┆ i32       ┆   ┆ str       ┆ u32       ┆ u32       ┆ list[i64 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2016      ┆ … ┆ AIR       ┆ 911       ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 16        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2016      ┆ … ┆ AIR       ┆ 911       ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 16        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2016      ┆ … ┆ AIR       ┆ 911       ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 16        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2017      ┆ … ┆ AIR       ┆ 925       ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 17        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000175 ┆ 000000175 ┆ AAR CORP  ┆ 2017      ┆ … ┆ AIR       ┆ 925       ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆           ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 17        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 000000180 ┆ 000000180 ┆ ABBOTT    ┆ 2019      ┆ … ┆ ABT       ┆ 1348      ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆ LABORATOR ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 19        ┆           ┆ IES       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000180 ┆ 000000180 ┆ ABBOTT    ┆ 2019      ┆ … ┆ ABT       ┆ 1348      ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆ LABORATOR ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 19        ┆           ┆ IES       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000180 ┆ 000000180 ┆ ABBOTT    ┆ 2020      ┆ … ┆ ABT       ┆ 1164      ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆ LABORATOR ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 20        ┆           ┆ IES       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000180 ┆ 000000180 ┆ ABBOTT    ┆ 2020      ┆ … ┆ ABT       ┆ 1164      ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆ LABORATOR ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 20        ┆           ┆ IES       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 000000180 ┆ 000000180 ┆ ABBOTT    ┆ 2020      ┆ … ┆ ABT       ┆ 1164      ┆ 5         ┆ [0, 1, … │
│ 0_10-K_20 ┆ 0         ┆ LABORATOR ┆           ┆   ┆           ┆           ┆           ┆ 10]      │
│ 20        ┆           ┆ IES       ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [89]:
## THIRD step: aggregation time with compound returns ! 


# Aggregate per (cik, name, fiscal_year, horizon)
lf_returns_summary = (
    lf_doc_returns_long
    .group_by(["cik", "name", "fiscal_year", "horizon"])
    .agg(
        n_docs     = pl.n_unique("docID"),
        mean_ret   = pl.mean("ret"),
        median_ret = pl.median("ret"),
        sd_ret     = pl.std("ret"),

        ## quantiles? - they give 
        p10        = pl.quantile("ret", 0.10, "nearest"),
        p90        = pl.quantile("ret", 0.90, "nearest"),

        # compounded return across docs: prod(1+r) - 1
        comp_ret   = ((pl.col("ret_safe") + 1).log().sum()).exp() - 1,
    )
    .with_columns(
        h_order = pl.col("horizon").str.replace("d", "").cast(pl.Int32)
    )
    # --> fixing sorting. .sort(["cik", "fiscal_year", "horizon"])
    .sort(["cik","fiscal_year","h_order"])
    # .drop("h_order")
)

#: quick peek / plan
# print(lf_returns_summary.explain())

returns_summary = lf_returns_summary.limit(limitval).collect()
returns_summary

## all numeric items are identical here bcs - grouping by (cik, name, fiscal_year) yields one event..



shape: (30, 12)
┌────────────┬────────────┬────────────┬─────────┬───┬───────────┬───────────┬───────────┬─────────┐
│ cik        ┆ name       ┆ fiscal_yea ┆ horizon ┆ … ┆ p10       ┆ p90       ┆ comp_ret  ┆ h_order │
│ ---        ┆ ---        ┆ r          ┆ ---     ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---     │
│ str        ┆ str        ┆ ---        ┆ str     ┆   ┆ f64       ┆ f64       ┆ f64       ┆ i32     │
│            ┆            ┆ i32        ┆         ┆   ┆           ┆           ┆           ┆         │
╞════════════╪════════════╪════════════╪═════════╪═══╪═══════════╪═══════════╪═══════════╪═════════╡
│ 0000001750 ┆ AAR CORP   ┆ 2016       ┆ 1d      ┆ … ┆ -0.081869 ┆ -0.081869 ┆ -0.081869 ┆ 1       │
│ 0000001750 ┆ AAR CORP   ┆ 2016       ┆ 5d      ┆ … ┆ -0.03115  ┆ -0.03115  ┆ -0.03115  ┆ 5       │
│ 0000001750 ┆ AAR CORP   ┆ 2016       ┆ 30d     ┆ … ┆ -0.052576 ┆ -0.052576 ┆ -0.052576 ┆ 30      │
│ 0000001750 ┆ AAR CORP   ┆ 2017       ┆ 1d      ┆ … ┆ 0.027012  ┆ 0.027012  ┆ 0.027012  ┆ 1       │
│ 0000001750 ┆ AAR CORP   ┆ 2017       ┆ 5d      ┆ … ┆ 0.006821  ┆ 0.006821  ┆ 0.006821  ┆ 5       │
│ …          ┆ …          ┆ …          ┆ …       ┆ … ┆ …         ┆ …         ┆ …         ┆ …       │
│ 0000001800 ┆ ABBOTT LAB ┆ 2019       ┆ 5d      ┆ … ┆ -0.080262 ┆ -0.080262 ┆ -0.080262 ┆ 5       │
│            ┆ ORATORIES  ┆            ┆         ┆   ┆           ┆           ┆           ┆         │
│ 0000001800 ┆ ABBOTT LAB ┆ 2019       ┆ 30d     ┆ … ┆ -0.289849 ┆ -0.289849 ┆ -0.289849 ┆ 30      │
│            ┆ ORATORIES  ┆            ┆         ┆   ┆           ┆           ┆           ┆         │
│ 0000001800 ┆ ABBOTT LAB ┆ 2020       ┆ 1d      ┆ … ┆ -0.022805 ┆ -0.022805 ┆ -0.022805 ┆ 1       │
│            ┆ ORATORIES  ┆            ┆         ┆   ┆           ┆           ┆           ┆         │
│ 0000001800 ┆ ABBOTT LAB ┆ 2020       ┆ 5d      ┆ … ┆ -0.024161 ┆ -0.024161 ┆ -0.024161 ┆ 5       │
│            ┆ ORATORIES  ┆            ┆         ┆   ┆           ┆           ┆           ┆         │
│ 0000001800 ┆ ABBOTT LAB ┆ 2020       ┆ 30d     ┆ … ┆ -0.031417 ┆ -0.031417 ┆ -0.031417 ┆ 30      │
│            ┆ ORATORIES  ┆            ┆         ┆   ┆           ┆           ┆           ┆         │
└────────────┴────────────┴────────────┴─────────┴───┴───────────┴───────────┴───────────┴─────────┘

In [90]:

# start from your materialized per-year summary
lf_yearly = returns_summary.lazy()

company_horizon_rollup = (
    lf_yearly
    .with_columns(
        h_order   = pl.col("horizon").str.replace("d", "").cast(pl.Int32),
        log1p_ret = (pl.col("comp_ret") + 1).log(),   # safe because you clipped earlier
    )
    .group_by(["cik", "name", "horizon", "h_order"])
    .agg(
        n_years = pl.n_unique("fiscal_year"),
        years   = pl.col("fiscal_year").unique().sort(),

        # across years (geometric)
        total_comp_ret = pl.col("log1p_ret").sum().exp() - 1,
        cagr           = pl.col("log1p_ret").mean().exp() - 1,

        # dispersion across years (uses mean_ret that you computed per year)
        mean_of_year_means = pl.mean("mean_ret"),
        sd_of_year_means   = pl.std("mean_ret"),
        p10_year           = pl.quantile("mean_ret", 0.10, "nearest"),
        p90_year           = pl.quantile("mean_ret", 0.90, "nearest"),

        # best/worst year via struct-sort (works in expression context)
        _best   = pl.struct(["fiscal_year", "mean_ret"]).sort_by("mean_ret", descending=True).first(),
        _worst  = pl.struct(["fiscal_year", "mean_ret"]).sort_by("mean_ret", descending=False).first(),
    )
    .with_columns(
        best_year = pl.col("_best").struct.field("fiscal_year"),
        best_ret  = pl.col("_best").struct.field("mean_ret"),
        worst_year= pl.col("_worst").struct.field("fiscal_year"),
        worst_ret = pl.col("_worst").struct.field("mean_ret"),
    )
    .drop(["_best","_worst"])
    .sort(["cik", "h_order"])
    .drop("h_order")
)

company_horizon_summary = company_horizon_rollup.collect()
company_horizon_summary.head(12)


shape: (6, 15)
┌────────────┬─────────────┬─────────┬─────────┬───┬───────────┬──────────┬────────────┬───────────┐
│ cik        ┆ name        ┆ horizon ┆ n_years ┆ … ┆ best_year ┆ best_ret ┆ worst_year ┆ worst_ret │
│ ---        ┆ ---         ┆ ---     ┆ ---     ┆   ┆ ---       ┆ ---      ┆ ---        ┆ ---       │
│ str        ┆ str         ┆ str     ┆ u32     ┆   ┆ i32       ┆ f64      ┆ i32        ┆ f64       │
╞════════════╪═════════════╪═════════╪═════════╪═══╪═══════════╪══════════╪════════════╪═══════════╡
│ 0000001750 ┆ AAR CORP    ┆ 1d      ┆ 5       ┆ … ┆ 2020      ┆ 0.04508  ┆ 2018       ┆ -0.100927 │
│ 0000001750 ┆ AAR CORP    ┆ 5d      ┆ 5       ┆ … ┆ 2017      ┆ 0.006821 ┆ 2018       ┆ -0.066941 │
│ 0000001750 ┆ AAR CORP    ┆ 30d     ┆ 5       ┆ … ┆ 2020      ┆ 0.058274 ┆ 2016       ┆ -0.052576 │
│ 0000001800 ┆ ABBOTT LABO ┆ 1d      ┆ 5       ┆ … ┆ 2018      ┆ 0.022891 ┆ 2019       ┆ -0.043296 │
│            ┆ RATORIES    ┆         ┆         ┆   ┆           ┆          ┆            ┆           │
│ 0000001800 ┆ ABBOTT LABO ┆ 5d      ┆ 5       ┆ … ┆ 2018      ┆ 0.027815 ┆ 2019       ┆ -0.080262 │
│            ┆ RATORIES    ┆         ┆         ┆   ┆           ┆          ┆            ┆           │
│ 0000001800 ┆ ABBOTT LABO ┆ 30d     ┆ 5       ┆ … ┆ 2017      ┆ 0.046387 ┆ 2019       ┆ -0.289849 │
│            ┆ RATORIES    ┆         ┆         ┆   ┆           ┆          ┆            ┆           │
└────────────┴─────────────┴─────────┴─────────┴───┴───────────┴──────────┴────────────┴───────────┘

In [ ]:
## END of chained practice. 

### Practicing and conv- to neatly formatted final query: PerDoc Analysis.

In [ ]:
# === FINALIZED VERSION: Per-document analysis with tidy long-form returns ===
# Purpose: Transform SEC filings data for panel analysis of stock returns

import polars as pl
DATA_PATH = "../data/exports/sec_filings_small_full.parquet"
KPI_CORE  = [10, 8, 9, 0, 1]  # Key sections: Notes, MD&A, FS, Business, Risk

# ============================================================================
# STAGE 1: BASE DATA PREPARATION
# ============================================================================
# Load data lazily and add fiscal year, filter to post-2015 and key sections
lf_base = (
    pl.scan_parquet(DATA_PATH)
    .with_columns(
        # Extract year from reportDate string
        pl.col("reportDate").str.strptime(pl.Date, strict=False).dt.year().alias("fiscal_year")
    )
    .filter(
        (pl.col("fiscal_year") > 2015) &  # Recent years only
        (pl.col("section").is_in(KPI_CORE))  # Key sections only
    )
)

# ============================================================================
# STAGE 2: DOCUMENT-LEVEL SENTENCE RANKING (Window Functions)
# ============================================================================
# Create positional indices within documents for sentence-level analysis
# IMPORTANT: Chain all operations - computed columns only exist within the chain
lf_first3_per_doc = (
    lf_base
    .sort(["docID", "sentenceCount"])  
    .with_columns([
        # Add computed fields
        pl.col("sentence").str.len_chars().alias("sentence_len"),
        pl.int_range(0, pl.len()).over("docID").alias("pos_in_doc"),  # 0-indexed position
        pl.int_range(0, pl.len()).over(["docID", "section"]).alias("pos_in_sect"),
    ])
    .with_columns([
        # Boolean flags for first sentences
        (pl.col("pos_in_doc") == 0).alias("is_first_in_doc"),
        (pl.col("pos_in_sect") == 0).alias("is_first_in_sect"),
    ])
    .filter(pl.col("pos_in_doc") < 3)  # Keep first 3 sentences per document
    .select(["docID", "pos_in_doc", "section", "sentence", "sentence_len"])
    .sort(["docID", "pos_in_doc"])
)

# ============================================================================
# STAGE 3: DOCUMENT-LEVEL RETURNS AGGREGATION
# ============================================================================
# Extract returns from nested structure and create document-grain table
# Returns are constant within a document (event-driven, not sentence-level)
lf_docs_returns = (
    lf_base
    .group_by("docID")
    .agg([
        # Document metadata (take first since constant within doc)
        pl.first("cik").alias("cik"),
        pl.first("name").alias("name"),
        pl.first("fiscal_year").alias("fiscal_year"),
        
        # Extract nested returns: returns.{1d|5d|30d}.ret
        # Structure: returns -> time_horizon -> ret (the actual return value)
        pl.col("returns").struct.field("1d").struct.field("ret").first().alias("ret_1d"),
        pl.col("returns").struct.field("5d").struct.field("ret").first().alias("ret_5d"),
        pl.col("returns").struct.field("30d").struct.field("ret").first().alias("ret_30d"),
    ])
)

# ============================================================================
# STAGE 4: RESHAPE TO TIDY/LONG FORMAT FOR PANEL ANALYSIS
# ============================================================================
# Transform from wide (ret_1d, ret_5d, ret_30d columns) to long format
# This creates one row per document × time_horizon combination
lf_doc_returns_long = (
    lf_docs_returns
    .unpivot(
        index=["docID", "cik", "name", "fiscal_year"],  # Keep these columns
        on=["ret_1d", "ret_5d", "ret_30d"],  # Pivot these to rows
        variable_name="horizon",  # New column for variable names
        value_name="ret",  # New column for values
    )
    .filter(pl.col("ret").is_not_null())  # Remove missing returns
    .with_columns([
        # Clean horizon labels: "ret_1d" -> "1d"
        pl.col("horizon").str.replace("^ret_", "").alias("horizon_clean"),
        
        # Clip returns to prevent numerical issues in compounding
        # (e.g., -1 would cause division by zero in (1+r) calculations)
        pl.col("ret").clip(lower_bound=-0.9999).alias("ret_safe"),
    ])
    .with_columns([
        # Extract numeric part for proper sorting (1, 5, 30)
        pl.col("horizon_clean").str.extract(r"(\d+)", 1).cast(pl.Int32).alias("h_order")
    ])
    .sort(["cik", "fiscal_year", "h_order"])  # Sort by company, year, horizon
    .select([
        # Final column selection
        "docID", "cik", "name", "fiscal_year",
        pl.col("horizon_clean").alias("horizon"),
        "ret", "ret_safe"
    ])
)

# ============================================================================
# USAGE EXAMPLES
# ============================================================================

print("="*60)
print("1. FIRST 3 SENTENCES PER DOCUMENT")
print("="*60)
first3 = lf_first3_per_doc.limit(15).collect()
print(first3)
print()

print("="*60)
print("2. DOCUMENT RETURNS IN LONG FORMAT (Panel-Ready)")
print("="*60)
doc_long = lf_doc_returns_long.limit(15).collect()
print(doc_long)
print()

# ============================================================================
# ADVANCED USAGE: Company-Horizon Summary Statistics
# ============================================================================
print("="*60)
print("3. COMPANY-LEVEL RETURN STATISTICS BY HORIZON")
print("="*60)

company_horizon_summary = (
    lf_doc_returns_long
    .with_columns(
        # Log returns for proper averaging (geometric mean)
        log1p_ret = (pl.col("ret_safe") + 1).log()
    )
    .group_by(["cik", "name", "horizon"])
    .agg([
        pl.n_unique("fiscal_year").alias("n_years"),
        pl.col("fiscal_year").unique().sort().alias("years"),
        
        # Compound return over all years: exp(sum(log(1+r))) - 1
        (pl.col("log1p_ret").sum().exp() - 1).alias("total_comp_ret"),
        
        # Compound annual growth rate: exp(mean(log(1+r))) - 1
        (pl.col("log1p_ret").mean().exp() - 1).alias("cagr"),
        
        # Simple statistics
        pl.mean("ret").alias("mean_ret"),
        pl.std("ret").alias("sd_ret"),
    ])
    .with_columns(
        # Extract numeric for sorting
        pl.col("horizon").str.extract(r"(\d+)", 1).cast(pl.Int32).alias("h_order")
    )
    .sort(["cik", "h_order"])
    .drop("h_order")
).collect()

print(company_horizon_summary.head(10))

1. FIRST 3 SENTENCES PER DOCUMENT
shape: (15, 5)
┌──────────────────────┬────────────┬─────────┬─────────────────────────────────┬──────────────┐
│ docID                ┆ pos_in_doc ┆ section ┆ sentence                        ┆ sentence_len │
│ ---                  ┆ ---        ┆ ---     ┆ ---                             ┆ ---          │
│ str                  ┆ i64        ┆ i64     ┆ str                             ┆ u32          │
╞══════════════════════╪════════════╪═════════╪═════════════════════════════════╪══════════════╡
│ 0000001750_10-K_2016 ┆ 0          ┆ 0       ┆ ITEM 1. BUSINESS (Dollars in m… ┆ 196          │
│ 0000001750_10-K_2016 ┆ 1          ┆ 0       ┆ AAR was founded in 1951, organ… ┆ 82           │
│ 0000001750_10-K_2016 ┆ 2          ┆ 0       ┆ We are a diversified provider … ┆ 116          │
│ 0000001750_10-K_2017 ┆ 0          ┆ 0       ┆ ITEM 1. BUSINESS General AAR C… ┆ 174          │
│ 0000001750_10-K_2017 ┆ 1          ┆ 0       ┆ AAR was founded in 1951, organ